In [1]:
import numpy as np
import pandas as pd
from preprocessing.wrangling import get_indi_df, get_labels, slide_and_flatten
from preprocessing.extract_features import get_all_ta_features, get_wavelet_coeffs
from evaluation.eval import sliding_window_cv_regression, batch_test_swcv_regression
from sklearn.metrics import mean_squared_error, mean_absolute_percentage_error, r2_score
from sklearn.preprocessing import StandardScaler, RobustScaler
from sklearn.feature_selection import SelectFromModel
from sklearn.linear_model import Lasso
from sklearn.ensemble import RandomForestRegressor
from numpy.lib.stride_tricks import sliding_window_view
from xgboost import XGBRegressor
from sklearn.pipeline import make_pipeline
import os

In [2]:
def add_closing_price(y, cls_price):
    return y + cls_price

In [9]:
class PersistanceModel:
    def __init__(self, persist_colname='Close'):
        self.persist_colname = persist_colname

    def __repr__(self):
        return "PersistanceModel(persist_colname={})".format(self.persist_colname)

    def fit(self, Xtr, ytr):
        pass

    def predict(self, Xts):
        return Xts.loc[:, self.persist_colname]


In [11]:
list_dir = 'data_collection/stocks_list'
list_prefix = "ind_nifty"
list_suffix = "list.csv"
save_dir = 'data_collection/ohlcv_data'
save_prefix = "ohlcv_"
save_suffix = ".csv"


for f in os.listdir(list_dir):
    if f.startswith(list_prefix) and f.endswith(list_suffix):
            savefile = os.path.join(save_dir, save_prefix+f[9:-8]+save_suffix)
            listfile = os.path.join(list_dir, f)
            p = pd.read_csv(listfile)
            symbols = list(p['Symbol'].values + '.NS')
            for symbol in symbols:
                df = get_indi_df(symbol, ohlcvfile=savefile, start_date="2017-01-01")
                df = get_all_ta_features(df)
                drop_columns = ['Date', 'Adj Close']
                df.drop(drop_columns, axis=1, inplace=True)
                move_dir_target, cls_target = get_labels(df['Close'])
                df = df.iloc[:-1]
                cls_target = cls_target.iloc[:-1]

                df10 = slide_and_flatten(df, window_len=10)
                df10 = pd.DataFrame(df10, index=df.index[9:])
                # df30 = slide_and_flatten(df, window_len=30)
                # df30 = pd.DataFrame(df30, index=df.index[29:])
                # df60 = slide_and_flatten(df, window_len=60)
                # df60 = pd.DataFrame(df60, index=df.index[59:])

                df10_wavelet = get_wavelet_coeffs(df['Close'], len_window=10, decomp_level=2)
                df10_wavelet = pd.DataFrame.from_records(df10_wavelet, index=df10.index)
                # df30_wavelet = get_wavelet_coeffs(df['Close'], len_window=30, decomp_level=2)
                # df30_wavelet = pd.DataFrame.from_records(df30_wavelet, index=df30.index)
                # df60_wavelet = get_wavelet_coeffs(df['Close'], len_window=60, decomp_level=2)
                # df60_wavelet = pd.DataFrame.from_records(df60_wavelet, index=df60.index)

                df10 = df10.merge(df10_wavelet, left_index=True, right_index=True)
                # df30 = df30.merge(df30_wavelet, left_index=True, right_index=True)
                # df60 = df60.merge(df60_wavelet, left_index=True, right_index=True)

                y = cls_target - df['Close']
                y10 = cls_target[9:] - df['Close'].iloc[9:]
                # y30 = cls_target[29:] - df['Close'].iloc[29:]
                # y60 = cls_target[59:] - df['Close'].iloc[59:]

                pipe1 = make_pipeline(
                    PersistanceModel(persist_colname="Close")
                )

                pipe2 = make_pipeline(
                    SelectFromModel(Lasso()),
                    (RobustScaler()),
                    (RandomForestRegressor())
                )


                batch_test_swcv_regression(
                    list_X = [df],
                    list_y = [cls_target],
                    list_pipe = [pipe1],
                    list_n_tr = [30],
                    list_n_ts = [1],
                    scorers = [mean_squared_error,mean_absolute_percentage_error, r2_score],
                    savefile='results/rfg_test_wavelet_{}.csv'.format(symbol),
                    comment_X=["persistance"],
                    list_post_processors=[None]
                )
                
                batch_test_swcv_regression(
                    list_X = [df10],
                    list_y = [y10],
                    list_pipe = [pipe2],
                    list_n_tr = [30],
                    list_n_ts = [1],
                    scorers = [mean_squared_error,mean_absolute_percentage_error, r2_score],
                    savefile='results/rfg_test_wavelet_{}.csv'.format(symbol),
                    comment_X=["df10_wavelet"],
                    list_post_processors=[(add_closing_price, {'cls_price':df['Close'].iloc[9:len(df)-(30+1)]})]
                )

                # cls_price should have length len(X)-(n_tr+n_ts)

/home/eee/anaconda3/lib/python3.9/site-packages/ta/trend.py:769: RuntimeWarning: invalid value encountered in double_scalars
  dip[idx] = 100 * (self._dip[idx] / value)
/home/eee/anaconda3/lib/python3.9/site-packages/ta/trend.py:774: RuntimeWarning: invalid value encountered in double_scalars
  din[idx] = 100 * (self._din[idx] / value)


A test completed. (Comment : ['persistance', 30, 1])


/home/eee/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:530: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 61.658460881378105, tolerance: 4.785941962687969
  model = cd_fast.enet_coordinate_descent(
/home/eee/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:530: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 59.87531034033231, tolerance: 4.32655345152537
  model = cd_fast.enet_coordinate_descent(
/home/eee/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:530: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 51.372114092478476, tolerance: 4.289073271450201
  model = cd_fast.enet_coordinate_descent(
/home/eee/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:5

3593     4505.258081
3594     4442.857476
3595     4503.713413
3596     4443.162793
3597     4438.306562
            ...     
4833    16764.941152
4834    17054.272715
4835    16433.888525
4836    16688.440586
4837    16158.820859
Name: Close, Length: 1245, dtype: float64 3593     4502.550293
3594     4449.299805
3595     4499.649902
3596     4436.799805
3597     4407.550293
            ...     
4833    17110.398438
4834    17108.699219
4835    15998.650391
4836    16490.851562
4837    15991.999023
Name: Close, Length: 1245, dtype: float64
A test completed. (Comment : ['df10_wavelet', 30, 1])


/home/eee/anaconda3/lib/python3.9/site-packages/ta/trend.py:769: RuntimeWarning: invalid value encountered in double_scalars
  dip[idx] = 100 * (self._dip[idx] / value)
/home/eee/anaconda3/lib/python3.9/site-packages/ta/trend.py:774: RuntimeWarning: invalid value encountered in double_scalars
  din[idx] = 100 * (self._din[idx] / value)


...

1251    100.937803
1252    101.804950
1253    101.697248
1254    101.450850
1255    103.641698
           ...    
2491    954.795527
2492    950.292010
2493    929.181975
2494    850.934518
2495    826.029984
Name: Close, Length: 1245, dtype: float64 1251    102.745003
1252     97.234993
1253    102.760002
1254    105.320000
1255    106.559998
           ...    
2491    967.299988
2492    975.750061
2493    975.999939
2494    878.700012
2495    806.000000
Name: Close, Length: 1245, dtype: float64
A test completed. (Comment : ['df10_wavelet', 30, 1])


/home/eee/anaconda3/lib/python3.9/site-packages/ta/trend.py:769: RuntimeWarning: invalid value encountered in double_scalars
  dip[idx] = 100 * (self._dip[idx] / value)
/home/eee/anaconda3/lib/python3.9/site-packages/ta/trend.py:774: RuntimeWarning: invalid value encountered in double_scalars
  din[idx] = 100 * (self._din[idx] / value)


A test completed. (Comment : ['persistance', 30, 1])


/home/eee/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:530: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.8210542449022115, tolerance: 0.00868502768747741
  model = cd_fast.enet_coordinate_descent(
/home/eee/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:530: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.820431904535536, tolerance: 0.00871032548155368
  model = cd_fast.enet_coordinate_descent(
/home/eee/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:530: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.8221640032184995, tolerance: 0.009379123709468402
  model = cd_fast.enet_coordinate_descent(
/home/eee/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_desc

ValueError: Found array with 0 feature(s) (shape=(30, 0)) while a minimum of 1 is required by RobustScaler.